In [1]:
import imageio
import numpy as np
import torch
from previous_skeleton import MentenSkeletonize, ShitSkeletonize, VitiSkeletonize
from morse_skeleton import DMTSkeletonize
from build import morse_complex as mc
from utils.functions import *
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from skel2graph import create_skeleton_graph, save_skeleton_graph
# autoreload from .py files
%load_ext autoreload
%autoreload 2

## Foreground Skeleton

In [2]:
# Three-dimensional example from the VESSAP dataset
img = np.load('data/image_vessap.npy')
img = torch.tensor(img, dtype=torch.float32).unsqueeze(0).unsqueeze(0)

### Menten Skeletonization

In [3]:
skeletonization_module = MentenSkeletonize(probabilistic=False, simple_point_detection='Boolean', num_iter=10)
skeleton = skeletonization_module(img)

mentenskeleton = skeleton.numpy().squeeze()

mentenskeleton_graph = create_skeleton_graph(mentenskeleton)
save_skeleton_graph(mentenskeleton_graph, 'images/mentenskeleton_vessap.vtp')
# np.save('data/mentenskeleton_vessap.npy', mentenskeleton)

### Shit Skeletonization

In [4]:
skeletonization_module = ShitSkeletonize(num_iter=10)
skeleton = skeletonization_module(img)

shitskeleton = skeleton.numpy().squeeze()
shitskeleton_graph = create_skeleton_graph(shitskeleton)
save_skeleton_graph(shitskeleton_graph, 'images/shitskeleton_vessap.vtp')
# np.save('data/shitskeleton_vessap.npy', shitskeleton)

### Viti Skeletonization

In [5]:
skeletonization_module = VitiSkeletonize(num_iter=10)
skeleton = skeletonization_module(img)

vitiskeleton = skeleton.numpy().squeeze()
vitiskeleton_graph = create_skeleton_graph(vitiskeleton)
save_skeleton_graph(vitiskeleton_graph, 'images/vitiskeleton_vessap.vtp')
# np.save('data/vitiskeleton_vessap.npy', vitiskeleton)

### Ours

In [6]:
skeletonization_module = DMTSkeletonize()

In [23]:
skeleton = skeletonization_module(img)
ourskeleton = skeleton.numpy().squeeze()
# np.save('data/vitiskeleton_vessap.npy', vitiskeleton)

In [7]:
threshold = 0
epsilon = 0
delta = -1

d = distance_transform(1-img[0,0,...].numpy()).astype(np.float32)
MC = mc.MorseComplex(d)
MC.process_lower_stars(10, 10, 10)

MC.prepare_morse_skeleton_below(threshold=threshold, epsilon=epsilon, delta=delta)
MC.extract_morse_skeleton_below(threshold=threshold, dimension=3)

pixels_below = np.array(MC.get_morse_skeleton_below())
ourskeleton = np.zeros_like(img[0,0,...])
ourskeleton[pixels_below[:,0], pixels_below[:,1], pixels_below[:,2]] = 1

ourskeleton_graph = create_skeleton_graph(ourskeleton)
save_skeleton_graph(ourskeleton_graph, 'images/DMTkeleton_vessap.vtp')


Canceling Pairs below 0 of persistence < 0:
Critical cells:
total: 273 686 476 62 --- < 0: 273 351 84 0 --- >= 0: 0 335 392 62                                      76 62 --- < 0: 392 470 84 0 --- >= 0: 0 335 392 62                    


In [25]:
# check if pixels_below is 1-dimensional or 2-dimensional array
if len(pixels_below.shape) == 1:
    pixels_below = np.array([pixels_below])

total: 273 686 476 62 --- < 0: 273 351 84 0 --- >= 0: 0 335 392 62                     


### Visualization

In [9]:
fig = make_subplots(
    rows=2, cols=3,
    specs=[[{'type': 'scatter3d'}, {'type': 'scatter3d'}, {'type': 'scatter3d'}],
           [{'type': 'scatter3d'}, {'type': 'scatter3d'}, {'type': 'scatter3d'}]],
    subplot_titles=("Image", "Menten et al.", "Shit et al.", "Viti et al.", "DMT (Ours)")
)

x_0, y_0, z_0 = np.where(img[0,0,...] == 1)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.1, mode='markers', marker=dict(size=2, color='blue'), name='Image'),
    row=1, col=1)

x_0, y_0, z_0 = np.where(mentenskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Menten et al.'),
    row=1, col=2)

x_0, y_0, z_0 = np.where(shitskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Shit et al.'),
    row=1, col=3)

x_0, y_0, z_0 = np.where(vitiskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Viti et al.'),
    row=2, col=1)

x_0, y_0, z_0 = np.where(ourskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='DMT (Ours)'),
    row=2, col=2)

fig.update_layout(
    autosize=True,
    margin=dict(
        l=0,  # left margin
        r=0,  # right margin
        b=0,  # bottom margin
        t=20,  # top margin
    ),
    # Optionally, adjust the plot's padding
    plot_bgcolor='white'
)
fig.show()

## Background Skeleton

In [27]:
# Three-dimensional example from the VESSAP dataset
img = np.load('data/image_vessap.npy')
img = 1-torch.tensor(img, dtype=torch.float32).unsqueeze(0).unsqueeze(0)

### Menten Skeletonization

In [28]:
skeletonization_module = MentenSkeletonize(probabilistic=False, simple_point_detection='Boolean', num_iter=10)
skeleton = skeletonization_module(img)

mentenskeleton = skeleton.numpy().squeeze()
# np.save('data/mentenskeleton_vessap.npy', mentenskeleton)

### Shit Skeletonization

In [29]:
skeletonization_module = ShitSkeletonize(num_iter=10)
skeleton = skeletonization_module(img)

shitskeleton = skeleton.numpy().squeeze()
# np.save('data/shitskeleton_vessap.npy', shitskeleton)

### Viti Skeletonization

In [30]:
skeletonization_module = VitiSkeletonize(num_iter=10)
skeleton = skeletonization_module(img)

vitiskeleton = skeleton.numpy().squeeze()
# np.save('data/vitiskeleton_vessap.npy', vitiskeleton)

### Ours

In [31]:
threshold = 0
epsilon = 0
delta = -1

d = distance_transform(1-img[0,0,...].numpy()).astype(np.float32)
MC = mc.MorseComplex(d)
MC.process_lower_stars(10, 10, 10)

MC.prepare_morse_skeleton_below(threshold=threshold, epsilon=epsilon, delta=delta)
MC.extract_morse_skeleton_below(threshold=threshold)

skeleton_pixels_below = MC.get_morse_skeleton_below()
ourskeleton = np.zeros_like(img[0,0,...])
for pixel in skeleton_pixels_below:
    ourskeleton[pixel[0], pixel[1], pixel[2]] = 1

In [ ]:
fig = make_subplots(
    rows=2, cols=3,
    specs=[[{'type': 'scatter3d'}, {'type': 'scatter3d'}, {'type': 'scatter3d'}],
           [{'type': 'scatter3d'}, {'type': 'scatter3d'}, {'type': 'scatter3d'}]],
    subplot_titles=("Image", "Menten et al.", "Shit et al.", "Viti et al.", "DMT (Ours)")
)

x_0, y_0, z_0 = np.where(img[0,0,...] == 1)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.1, mode='markers', marker=dict(size=2, color='blue'), name='Image'),
    row=1, col=1)

x_0, y_0, z_0 = np.where(mentenskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Menten et al.'),
    row=1, col=2)

x_0, y_0, z_0 = np.where(shitskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Shit et al.'),
    row=1, col=3)

x_0, y_0, z_0 = np.where(vitiskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='Viti et al.'),
    row=2, col=1)

x_0, y_0, z_0 = np.where(ourskeleton >0.0)
fig.add_trace(go.Scatter3d(x=x_0, y=y_0, z=z_0, opacity=0.25, mode='markers', marker=dict(size=2, color='red'), name='DMT (Ours)'),
    row=2, col=2)

fig.update_layout(
    autosize=True,
    margin=dict(
        l=0,  # left margin
        r=0,  # right margin
        b=0,  # bottom margin
        t=20,  # top margin
    ),
    # Optionally, adjust the plot's padding
    plot_bgcolor='white'
)
fig.show()

total: 732 1499 855 87 --- < 0: 732 1393 647 0 --- >= 0: 0 106 208 87                       
